In [1]:
import argparse
from typing import Optional, Union

import pandas as pd
import numpy as np
import torch
import torch.nn as nn

from dataclasses import dataclass

import datasets
from datasets import Dataset
from torch.utils.data import Dataset, DataLoader

from sklearn.metrics import log_loss

from transformers import (
    AutoTokenizer,
    AutoConfig,
    EarlyStoppingCallback,
    AutoModelForCausalLM,
    AutoModelForMultipleChoice,
    TrainingArguments,
    Trainer,
    RobertaForMultipleChoice,
    AutoModelForSequenceClassification,
    LlamaModel,
    LlamaForSequenceClassification,
    BitsAndBytesConfig,
    get_polynomial_decay_schedule_with_warmup,
    get_cosine_schedule_with_warmup,
    TrainerCallback,
)
from transformers.tokenization_utils_base import PreTrainedTokenizerBase, PaddingStrategy

from peft import (
    get_peft_config,
    PeftModel,
    PeftConfig,
    get_peft_model,
    LoraConfig,
    TaskType,
)
import os

import random
def seed_everything(seed=None):
    '''
    固定seed
    :param seed: int, 随机种子
    '''
    max_seed_value = np.iinfo(np.uint32).max
    min_seed_value = np.iinfo(np.uint32).min

    if (seed is None) or not (min_seed_value <= seed <= max_seed_value):
        seed = random.randint(np.iinfo(np.uint32).min, np.iinfo(np.uint32).max)
    os.environ["PYTHONHASHSEED"] = str(seed)
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True
    return seed


seed_everything(42)

42

In [2]:
from torch.utils.data import Dataset
class InstructionDataSet(Dataset):
    def __init__(self, data, tokenizer, max_source_length, max_target_length):
        super(InstructionDataSet, self).__init__()
        #self.data = data.sample(len(data), random_state=0).reset_index(drop=True)
        self.data = data
        self.tokenizer = tokenizer
        self.max_source_length = max_source_length
        self.max_target_length = max_target_length
        # self.A_token = self.tokenizer.encode(text='A', add_special_tokens=False, truncation=True, )
        # self.B_token = self.tokenizer.encode(text='B', add_special_tokens=False, truncation=True, )
        # self.C_token = self.tokenizer.encode(text='C', add_special_tokens=False, truncation=True, )

    def __len__(self):
        return len(self.data)

    def __getitem__(self, index):
        now_data = self.data.loc[index]
        idx = now_data['id']
        r_a = now_data['instruction_a']
        r_b = now_data['instruction_b']
        
        templete_part1 = "<|begin_of_text|><|start_header_id|>user<|end_header_id|>\n\nHere are two question-answering dialogues. Compare two model performance on answering question, determine which is better.\n\n"
        templete_part1_input_ids = self.tokenizer(text=templete_part1, add_special_tokens=True, padding=False)['input_ids']
        
        model_a_input_ids = self.tokenizer(text=r_a, add_special_tokens=True, truncation=True,
                                          max_length=self.max_source_length // 2, padding=False)['input_ids']
        model_b_input_ids = self.tokenizer(text=r_b, add_special_tokens=True, truncation=True,
                                          max_length=self.max_source_length // 2, padding=False)['input_ids']
        templete_part2 = "###options\nA. Model A\nB. Model B\nC. Tie\n<|eot_id|>\n<|start_header_id|>assistant<|end_header_id|>"
        templete_part2_input_ids = self.tokenizer(text=templete_part2, add_special_tokens=True, padding=False)['input_ids']
        
        input_ids = templete_part1_input_ids + model_a_input_ids + model_b_input_ids + templete_part2_input_ids
        input_text = self.tokenizer.decode(input_ids, skip_special_tokens=False)
        print(f"input :\n {input_text}")
        return {
            "input_ids": input_text,
            "id": idx
        }

In [3]:
from typing import Any, Callable, Dict, List, NewType, Optional, Tuple, Union
# @dataclass
# class DataCollatorForInstruction:
#     tokenizer: PreTrainedTokenizerBase
#     model: Optional[Any] = None
#     padding: Union[bool, str, PaddingStrategy] = True
#     max_length: Optional[int] = None
#     pad_to_multiple_of: Optional[int] = None
#     label_pad_token_id: int = -100
#     return_tensors: str = "pt"

#     def __call__(self, features, return_tensors=None):
#         if return_tensors is None:
#             return_tensors = self.return_tensors
#         labels = [feature["labels"] for feature in features] if "labels" in features[0].keys() else None
#         print(f"features is {features}")
#         # We have to pad the labels before calling `tokenizer.pad` as this method won't pad them and needs them of the
#         # same length to return tensors.

# #         features = self.tokenizer(
# #             features,
# #             padding='longest',
# #             max_length=MAX_LENGTH,
# #             pad_to_multiple_of=self.pad_to_multiple_of,
# #             return_tensors=return_tensors,
# #             truncation=True
# #         )

#         # prepare decoder_input_ids
#         if (
#                 labels is not None
#                 and self.model is not None
#                 and hasattr(self.model, "prepare_decoder_input_ids_from_labels")
#         ):
#             decoder_input_ids = self.model.prepare_decoder_input_ids_from_labels(labels=features["labels"])
#             features["decoder_input_ids"] = decoder_input_ids
#         # breakpoint() # [(len(features[i]['input_ids']),len(features[i]['labels'])) for i in range(4)]
#         return features


def collate_fn(batch):
    batch = {k: [item[k] for item in batch] for k in ('input_ids','id')}
    batch_input = tokenizer(
        batch['input_ids'],
        padding='longest',
        truncation=True,
        return_tensors="pt",
        add_special_tokens=True,
        max_length=MAX_LENGTH + 50
    )
    return batch_input, batch['id']

In [4]:
test = pd.read_csv('dataset/random_instruction_valid.csv')#.sample(5).reset_index(drop = True)
#test = test.groupby('id').head(1).reset_index(drop = True)
#test = test.loc[:500,:].reset_index(drop=True)
#sample_sub = pd.read_csv('/kaggle/input/lmsys-chatbot-arena/sample_submission.csv')

In [5]:
from tqdm import tqdm
def inference(model, test_dataloader):
    test_predictions = []
    for batch in tqdm(test_dataloader):
        batch_input, idx = batch
        for k in batch_input.keys():
            batch_input[k] = batch_input[k].to(device)
        with torch.no_grad():
            #batch_input, idx = batch['input_ids'], batch['id']
            #batch_input = {"input_ids": batch_input}
            #logits = outputs.logits.cpu().detach().numpy()
            response = model.generate(**batch_input, max_new_tokens=1, return_dict_in_generate=True, output_scores=True)
            #batch_input['input_ids'].shape[-1] + 1
            #print(f"score {response.scores}")
            #print(f"score is {response.scores[0]}")
            #print(f"response is {response}")
            #redict = np.exp(logits) / np.sum(np.exp(logits), axis=-1, keepdims=True)
            score = response.scores[0]
            A_prob, B_prob, C_prob = score[:,A_TOKEN_IDS], score[:,B_TOKEN_IDS], score[:,C_TOKEN_IDS]
            logits = torch.Tensor([[A_prob,B_prob,C_prob]])
            logits = torch.softmax(logits, dim=-1).cpu().numpy()
            print(f"logits is {logits}")
            node_result = [[idx[i],logits[i]] for i in range(batch_size)]

        test_predictions.append(node_result)
    return test_predictions

In [6]:
device = torch.device("cuda:0")

In [7]:
base_model = 'meta-llama/llama-3-transformers-8b-hf-v1'
model_path = "output/rare-wind-117/checkpoint-8400"
MAX_LENGTH = 1500

In [8]:
tokenizer = AutoTokenizer.from_pretrained(model_path)
config = AutoConfig.from_pretrained(base_model, trust_remote_code=True)

bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,  
    bnb_4bit_quant_type='nf4',
    bnb_4bit_compute_dtype=torch.float16,
    bnb_4bit_use_double_quant=False
)
base_model_0 = AutoModelForCausalLM.from_pretrained(base_model,
                                                 config=config,
                                                 quantization_config=bnb_config,
                                                 torch_dtype=torch.float16,
                                                 device_map="auto",
                                                 trust_remote_code=True)
base_model_0.config.pad_token_id = tokenizer.pad_token_id
base_model_0.resize_token_embeddings(len(tokenizer))
new_model = model_path
model0 = PeftModel.from_pretrained(base_model_0, new_model).to(device)
#model0 = model0.merge_and_unload()
model0.eval()

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

PeftModelForSequenceClassification(
  (base_model): LoraModel(
    (model): LlamaForCausalLM(
      (model): LlamaModel(
        (embed_tokens): Embedding(128257, 4096)
        (layers): ModuleList(
          (0-31): 32 x LlamaDecoderLayer(
            (self_attn): LlamaSdpaAttention(
              (q_proj): lora.Linear4bit(
                (base_layer): Linear4bit(in_features=4096, out_features=4096, bias=False)
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.05, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=4096, out_features=16, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=16, out_features=4096, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
              )
              (k_proj): lora.Linear4bit(
                (base_

In [9]:
A_TOKEN_IDS = tokenizer('A',add_special_tokens=True, truncation=True, max_length=1024)['input_ids']
B_TOKEN_IDS = tokenizer('B',add_special_tokens=True, truncation=True, max_length=1024)['input_ids']
C_TOKEN_IDS = tokenizer('C',add_special_tokens=True, truncation=True, max_length=1024)['input_ids']


In [10]:
A_TOKEN_IDS,B_TOKEN_IDS,C_TOKEN_IDS

([32], [33], [34])

In [11]:
tokenizer = AutoTokenizer.from_pretrained(model_path)
tokenized_dataset = InstructionDataSet(test, tokenizer, MAX_LENGTH, 1)

token_ids = tokenized_dataset[0]['input_ids']
tokens = tokenizer.convert_ids_to_tokens(token_ids)

for token, token_id in zip(tokens, token_ids):
    print(f"Token: {token}, ID: {token_id}")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


input :
 <|begin_of_text|><|start_header_id|>user<|end_header_id|>

Here are two question-answering dialogues. Compare two model performance on answering question, determine which is better.

###Model A
Prompt: Is it morally right to try to have a certain percentage of females on managerial positions?
Response: The question of whether it is morally right to aim for a certain percentage of females in managerial positions is a complex ethical issue that involves considerations of fairness, equality, diversity, and discrimination.\n\nHere are some arguments in favor of and against such policies:\n\n**Arguments in favor:**\n\n1. **Correcting Historical Inequities:** Women have historically been underrepresented in leadership roles due to various cultural, institutional, and social barriers. Aiming for a specific percentage can be seen as a corrective measure to address past and ongoing discrimination.\n\n2. **Promoting Diversity:** Diverse leadership teams can enhance decision-making and r

ValueError: invalid literal for int() with base 10: '<'

In [12]:
batch_size = 1
tokenized_dataset = InstructionDataSet(test, tokenizer, MAX_LENGTH, 1)

test_dataloader = torch.utils.data.DataLoader(tokenized_dataset, batch_size = batch_size ,collate_fn=collate_fn)

In [ ]:
sub_pred = inference(model = model0, test_dataloader = test_dataloader)

logits is [[0.50443983 0.24971582 0.24584433]]
input :
 <|begin_of_text|><|start_header_id|>user<|end_header_id|>

Here are two question-answering dialogues. Compare two model performance on answering question, determine which is better.

###Model A
Prompt: what is a green thing you might find in an office?
Response: A common green object you might find in an office could be a plant, such as a succulent or a fern. Other green items could include a stapler, a notebook, a pen, or a desk organizer.

###Model B
Prompt: what is a green thing you might find in an office?
Response: There are several green things that you might find in an office, depending on the specific office and its policies. Some examples of green things you might find in an office include:\n\n1. Energy-efficient lighting: Many offices have upgraded to energy-efficient lighting options, such as LED bulbs, to reduce energy consumption and lower their carbon footprint.\n2. Recycled materials: Some offices may use recycled m

 43%|████▎     | 1507/3544 [03:45<05:21,  6.34it/s]Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


logits is [[0.5155439  0.25923175 0.22522445]]
input :
 <|begin_of_text|><|start_header_id|>user<|end_header_id|>

Here are two question-answering dialogues. Compare two model performance on answering question, determine which is better.

###Model A
Prompt: How much is 6+5*4-3\/2+1?
Response: To solve the expression 6 + 5 * 4 - 3 \/ 2 + 1, we need to follow the order of operations, which is often remembered by the acronym PEMDAS (Parentheses, Exponents, Multiplication and Division from left to right, Addition and Subtraction from left to right).\n\nSo, we start with multiplication and division first, then move on to addition and subtraction:\n\n1. Multiplication: 5 * 4 = 20\n2. Division: 3 \/ 2 = 1.5\n\nNow the expression looks like this: 6 + 20 - 1.5 + 1\n\nNext, we perform addition and subtraction from left to right:\n\n1. Addition: 6 + 20 = 26\n2. Subtraction: 26 - 1.5 = 24.5\n3. Addition: 24.5 + 1 = 25.5\n\nThe final result of the expression is 25.5.

###Model B
Prompt: How much is

 43%|████▎     | 1509/3544 [03:45<05:25,  6.25it/s]Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


logits is [[0.50726706 0.20818198 0.28455102]]
input :
 <|begin_of_text|><|start_header_id|>user<|end_header_id|>

Here are two question-answering dialogues. Compare two model performance on answering question, determine which is better.

###Model A
Prompt: there anything necessary in bell peppers? If bell peppers have to be replaced due to allergies to bell pepper, cayane pepper, paprika, etc... what is recommended replacement?"]
Response: ll peppers are a good source of vitamins A and C, potassium, folic acid, and fiber. They also contain a variety of phytonutrients that have antioxidant properties. If you need to replace bell peppers due to allergies to bell peppers, cayenne pepper, paprika, and other foods in the nightshade family, you can consider the following alternatives to provide similar nutritional benefits:\n\n1. **Squash**: Varieties like butternut, acorn, or zucchini can provide beta-carotene and vitamin C. They can be roasted, steamed, or saut\u00e9ed and added to dishes

...

 99%|█████████▉| 3525/3544 [08:57<00:02,  6.70it/s]Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


logits is [[0.30166543 0.43211576 0.2662188 ]]
input :
 <|begin_of_text|><|start_header_id|>user<|end_header_id|>

Here are two question-answering dialogues. Compare two model performance on answering question, determine which is better.

###Model A
Prompt: Solve this murder mystery riddle:\n\nA man was found murdered one Sunday morning. His wife immediately called the police. The police questioned the wife and staff. The wife said she was sleeping, the cook said he was cooking breakfast, the gardener said he was planting seeds, the maid said she was getting the mail, and the butler said he was polishing the silverware.\n\nThe police immediately arrested the murderer. Who did it and how did they know?
Response: The butler did it.\n\nThe clue here is that everyone was doing their regular tasks. The butler's job is to polish the silverware, which is typically done on Sundays. The other staff members also mentioned their regular duties (cooking breakfast, planting seeds, getting the mail)

 99%|█████████▉| 3526/3544 [08:58<00:02,  7.19it/s]Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


logits is [[0.5424854  0.20914675 0.24836792]]
input :
 <|begin_of_text|><|start_header_id|>user<|end_header_id|>

Here are two question-answering dialogues. Compare two model performance on answering question, determine which is better.

###Model A
Prompt: explain to me how regression to the mean can be addressed by empirical dynamical models
Response: Regression to the mean is a phenomenon that occurs when a variable that is observed to be extreme in one time period is likely to be less extreme in the next time period. This can lead to a bias in statistical models, as the extreme value is not representative of the long-term average behavior of the variable. Empirical dynamical models (EDMs) are a type of statistical model that can address this issue by incorporating information about the underlying dynamics of the system being modeled.\n\nEDMs are based on the idea that the behavior of a system can be described by a set of underlying dynamics, such as physical laws or mechanistic rel

100%|█████████▉| 3528/3544 [08:58<00:02,  6.33it/s]Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


In [ ]:
# 提取数据
processed_data = []
for item in sub_pred:
    item = item[0]
    id = item[0].item()  # 获取id
    array_values = item[1].tolist()  # 获取array并转换为列表
    processed_data.append([id] + array_values)

In [19]:
new_columns = ['id', 'winner_model_a', 'winner_model_b', 'winner_tie']
df = pd.DataFrame(processed_data, columns=new_columns)

In [20]:
df = df.groupby('id').mean().reset_index()

In [21]:
df

id  winner_model_a  winner_model_b  winner_tie
0          30192        0.867288        0.058105    0.074608
1        1256092        0.825098        0.050331    0.124571
2        3258431        0.632957        0.115270    0.251773
3        4186011        0.191948        0.610010    0.198041
4        5717448        0.325730        0.386814    0.287456
...          ...             ...             ...         ...
2869  4287311513        0.418304        0.357794    0.223902
2870  4289792977        0.336595        0.375499    0.287905
2871  4291367819        0.259377        0.532207    0.208415
2872  4292709507        0.325357        0.269730    0.404913
2873  4293918673        0.863340        0.026898    0.109761

[2874 rows x 4 columns]

In [22]:
str2num = {'A':0, "B":1, "C":2}

In [23]:
test['label_number'] = test.label.map(str2num)

In [24]:
from sklearn.metrics import log_loss

In [25]:
prediction = np.array(df[new_columns[1:]])

In [26]:
test = test.drop_duplicates(subset = ['id']).reset_index(drop = True)

In [27]:
log_loss(test.label_number, prediction)

/root/miniconda3/lib/python3.10/site-packages/sklearn/metrics/_classification.py:2981: UserWarning: The y_pred values do not sum to one. Starting from 1.5 thiswill result in an error.
  warnings.warn(


0.9789625226905673

In [ ]:
3.176938522630114

In [ ]:
test['label'][:12]